In [201]:
%matplotlib osx
import matplotlib.pyplot as plt
import numpy as np
import math
from matplotlib.animation import FFMpegWriter
from mpl_toolkits.mplot3d import Axes3D
from matplotlib import cm

In [289]:
mS = 1e7
mP = 1e4
mA = 0.1
G = 1
theta = math.radians(-20)

R = 25
xS = 0
yS = 0
xP = 20
yP = 0
rS = np.array([xS,yS])
rP = np.array([xP,yP])


rCM = (rP*mP + rS*mS) / (mP+mS)
rS = rS - rCM
rP = rP - rCM

xA = R * math.cos(theta)
yA = R * math.sin(theta)
rA = np.array([xA,yA])

print(rS)
print(rP)
print(rA)

[-0.01998002  0.        ]
[19.98001998  0.        ]
[23.49231552 -8.55050358]


In [290]:
mu = (mS*mP)/(mS+mP)
omega = math.sqrt((G*mS*mP)/(mu*R**3))

vS_n = omega * np.linalg.norm(rS)
vP_n = omega * np.linalg.norm(rP)
vA_n = omega * np.linalg.norm(rA)

vS = vS_n * np.array([0,-1])
vP = vP_n * np.array([0,1])
vA = vA_n * np.array([0,0.8])

xS = rS[0]
yS = rS[1]
xP = rP[0]
yP = rP[1]
xA = rA[0]
yA = rA[1]

vSx = vS[0]
vSy = vS[1]
vPx = vP[0]
vPy = vP[1]
vAx = vA[0]
vAy = vA[1]

y = np.array([xS,yS,vSx,vSy,xP,yP,vPx,vPy,xA,yA,vAx,vAy])
print(y)

[-1.99800200e-02  0.00000000e+00  0.00000000e+00 -5.05711633e-01
  1.99800200e+01  0.00000000e+00  0.00000000e+00  5.05711633e+02
  2.34923155e+01 -8.55050358e+00  0.00000000e+00  5.06217345e+02]


In [291]:
def KeplerODE(t,y):
    global mA,mP,mS,G

    rS = y[0:2]
    vS = y[2:4]
    rP = y[4:6]
    vP = y[6:8]
    rA = y[8:10]
    vA = y[10:12]

    drdtS = vS
    drdtP = vP
    drdtA = vA

    FS    = - mS*mP*G / np.linalg.norm(rS-rP)**3 * (rS-rP) - mS*mA*G / np.linalg.norm(rS-rA)**3 * (rS-rA)
    FP    = - mP*mS*G / np.linalg.norm(rP-rS)**3 * (rP-rS) - mP*mA*G / np.linalg.norm(rP-rA)**3 * (rP-rA)
    FA    = - mA*mS*G / np.linalg.norm(rA-rS)**3 * (rA-rS) - mA*mP*G / np.linalg.norm(rA-rP)**3 * (rA-rP)
    
    aS    = FS / mS
    aP    = FP / mP
    aA    = FA / mA
    
    dvdtS = aS
    dvdtP = aP
    dvdtA = aA
    
    S = np.concatenate((drdtS,dvdtS))
    P = np.concatenate((drdtP,dvdtP))
    A = np.concatenate((drdtA,dvdtA))
    
    tmp = np.concatenate((S,P))
    
    return np.concatenate((tmp,A))
    
KeplerODE(0,y)

array([ 0.00000000e+00, -5.05711633e-01,  2.50001501e+01, -5.46001098e-05,
        0.00000000e+00,  5.05711633e+02, -2.49999996e+04, -1.08253996e-03,
        0.00000000e+00,  5.06217345e+02, -1.50584829e+04,  5.56826498e+03])

In [292]:
global mA,mP,mS,G,y
P = math.sqrt((4*math.pi**2*R**3)/(G*(mS+mP)))
dt = P/1000
tMAX = P/2
t = 0

xSt = []
ySt = []
xPt = []
yPt = []
xAt = []
yAt = []
tt = []

while (t < tMAX):
    xSt.append(y[0])
    ySt.append(y[1])
    xPt.append(y[4])
    yPt.append(y[5])
    xAt.append(y[8])
    yAt.append(y[9])
    
    f1 = KeplerODE(t       ,y          )
    f2 = KeplerODE(t+dt/2.0,y+f1*dt/2.0)
    f3 = KeplerODE(t+dt/2.0,y+f2*dt/2.0)
    f4 = KeplerODE(t+dt    ,y+f3*dt    )
    
    y = y + (f1 + 2.0*f2 + 2.0*f3 + f4) / 6.0 * dt
    t = t + dt
    

plt.plot(xSt,ySt,'r-')
plt.plot(xPt,yPt,'b-')
plt.plot(xAt,yAt,'g-')
plt.gca().set_aspect('equal', adjustable='box')
plt.show()

In [224]:
metadata = dict(title='test', artist='test',comment='test')
writer = FFMpegWriter(fps=15, metadata=metadata)
fig = plt.figure()

global mA,mP,mS,G,y
P = math.sqrt((4*math.pi**2*R**3)/(G*(mS+mP)))
dt = P/1000
tMAX = P/4
t = 0

xSt = []
ySt = []
xPt = []
yPt = []
xAt = []
yAt = []
tt = []

fig = plt.figure(dpi=200)

with writer.saving(fig, "test.mp4", dpi=200):
    while (t < tMAX):
        xSt.append(y[0])
        ySt.append(y[1])
        xPt.append(y[4])
        yPt.append(y[5])
        xAt.append(y[8])
        yAt.append(y[9])

        f1 = KeplerODE(t       ,y          )
        f2 = KeplerODE(t+dt/2.0,y+f1*dt/2.0)
        f3 = KeplerODE(t+dt/2.0,y+f2*dt/2.0)
        f4 = KeplerODE(t+dt    ,y+f3*dt    )

        y = y + (f1 + 2.0*f2 + 2.0*f3 + f4) / 6.0 * dt
        t = t + dt

        plt.plot(xSt,ySt,'r-')
        #plt.plot(xPt,yPt,'b-')
        plt.plot(xAt,yAt,'g-')
        plt.draw()
        plt.pause(0.01)
        writer.grab_frame()

    

"""plt.plot(xSt,ySt,'r-')
plt.plot(xPt,yPt,'b-')
plt.plot(xAt,yAt,'g-')
plt.gca().set_aspect('equal', adjustable='box')
plt.show()"""


"""plt.ion()

fig = plt.figure()
ax = fig.add_subplot(111)
line1, = ax.plot(xSt,ySt)
line2, = ax.plot(xPt,yPt)
line3, = ax.plot(xAt,yPt)

for _ in range(500):
    line1.set_xdata(xSt)
    line1.set_ydata(ySt)
    line2.set_xdata(xPt)
    line2.set_ydata(yPt)
    line3.set_xdata(xAt)
    line3.set_ydata(yAt)

    fig.canvas.draw()
    
    fig.canvas.flush_events()
    time.sleep(0.1)
"""

'plt.ion()\n\nfig = plt.figure()\nax = fig.add_subplot(111)\nline1, = ax.plot(xSt,ySt)\nline2, = ax.plot(xPt,yPt)\nline3, = ax.plot(xAt,yPt)\n\nfor _ in range(500):\n    line1.set_xdata(xSt)\n    line1.set_ydata(ySt)\n    line2.set_xdata(xPt)\n    line2.set_ydata(yPt)\n    line3.set_xdata(xAt)\n    line3.set_ydata(yAt)\n\n    fig.canvas.draw()\n    \n    fig.canvas.flush_events()\n    time.sleep(0.1)\n'